In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'GrossProfit', u'營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
('year:', 107)
('season:', 4)
營業毛利（毛損）
('year:', 107)
('season:', 3)
營業毛利（毛損）
('year:', 107)
('season:', 2)
營業毛利（毛損）
('year:', 107)
('season:', 1)
營業毛利（毛損）
('year:', 106)
('season:', 4)
營業毛利（毛損）
('year:', 106)
('season:', 3)
營業毛利（毛損）
('year:', 106)
('season:', 2)
營業毛利（毛損）
('year:', 106)
('season:', 1)
營業毛利（毛損）
('year:', 105)
('season:', 4)
營業毛利（毛損）
('year:', 105)
('season:', 3)
營業毛利（毛損）
('year:', 105)
('season:', 2)
營業毛利（毛損）
('year:', 105)
('season:', 1)


公司代號      公司名稱 GrossProfit_108Q1 GrossProfit_107Q4 GrossProfit_107Q3  \
0    2801      彰化銀行               NaN               NaN               NaN   
1    2809      京城銀行               NaN               NaN               NaN   
2    2812      台中銀行               NaN               NaN               NaN   
3    2820        華票               NaN               NaN               NaN   
4    2834      臺灣企銀               NaN               NaN               NaN   
5    2836        高銀               NaN               NaN               NaN   
6    2838      聯邦銀行               NaN               NaN               NaN   
7    2845      遠東商銀               NaN               NaN               NaN   
8    2849      安泰銀行               NaN               NaN               NaN   
9    2855      統一證券               NaN               NaN               NaN   
10   6005       群益證               NaN               NaN               NaN   
11   6024       群益期               NaN               NaN               NaN   
12   1101        台泥           6487864          33591539          24664574   
13   1102        亞泥           4658501          21156314          14927303   
14   1103        嘉泥             65221            288488            219450   
15   1104      環球水泥            106420            571082            405283   
16   1108      幸福水泥             26663             46767             69600   
17   1109      信大水泥            389325           2183831           1440912   
18   1110        東泥             34933            144454             94110   
19   1201      味全公司           1349864           6038549           4570208   
20   1203      味王公司            463801           1970005           1484790   
21   1210      大成長城           2655076          10088095           7575085   
22   1215      卜蜂企業            722603           2857350           2050106   
23   1216        統一          37102312         145284867         112619748   
24   1217       愛之味            308201           1380563           1162124   
25   1218      泰山企業            313782           1433034           1137533   
26   1219      福壽實業            263446            790072            595584   
27   1220        台榮             68135            337316            246578   
28   1225       福懋油            242787            910621            642572   
29   1227        佳格           2235865           8254345           5986375   
30   1229      聯華實業            201314            832057            613323   
31   1231      聯華食品            443541           1778074           1282762   
32   1232       大統益            567605           1857028           1306751   
33   1233        天仁            331040           1256139            947455   
34   1234        黑松            446503           2117661           1873142   
35   1235        興泰                89             26761             27119   
36   1236      宏亞食品            123815            526897            338526   
37   1256   鮮活果汁-KY            247025           1144096            944335   
38   1262     綠悅-KY            -45818            -21899             30806   
39   1301        台塑           8147624          37308068          29305335   
40   1303      南亞塑膠           6515317          49007295          40342413   
41   1304        台聚           1560360           5794740           4929008   
42   1305        華夏            448517           2702563           2305108   
43   1307      三芳化工            530041           1927908           1426618   
44   1308        亞聚            176893            284466            182252   
45   1309      台達化工            393182           1043743           1048143   
46   1310        台苯            448128           1976994           1839176   
47   1312      國喬石化            691297           4055348           3448068   
48   1313        聯成            242260           3104865           2767775   
49   1314       中石化            307990           5176162           4442076   
50   1315      達新工業             81941            382079            295133   
5

In [5]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_eps_sii.columns # the column index
#idx = df_eps_sii.index # the row index
numOfRows_s = df_gross_profit_sii.shape[0] #len(df_gross_profit_sii) #len(df_gross_profit_sii.index)
numOfColumns_s = df_gross_profit_sii.shape[1] #len(df_gross_profit_sii.columns)
headNameOfColumns_s = df_gross_profit_sii.columns

print(numOfColumns_s)
df_gross_profit_sii

for row_index_s in range(0, numOfRows_s):
    for col_index_s in range(0, numOfColumns_s):
        #print(df_gross_profit_sii.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_gross_profit_sii.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_gross_profit_sii.columns.values[col_index_s]): # if (df_eps_sii.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_gross_profit_sii.columns.values[col_index_s]):
                continue
            elif (u"公司名稱" in df_gross_profit_sii.columns.values[col_index_s]):
                continue
            elif (col_index_s == numOfColumns_s-1):
                continue
            else:
                df_gross_profit_sii.iloc[row_index_s, col_index_s] = float(df_gross_profit_sii.iloc[row_index_s, col_index_s]) - float(df_gross_profit_sii.iloc[row_index_s, col_index_s+1])

df_gross_profit_sii              

15


公司代號      公司名稱 GrossProfit_108Q1 GrossProfit_107Q4 GrossProfit_107Q3  \
0    2801      彰化銀行               NaN               NaN               NaN   
1    2809      京城銀行               NaN               NaN               NaN   
2    2812      台中銀行               NaN               NaN               NaN   
3    2820        華票               NaN               NaN               NaN   
4    2834      臺灣企銀               NaN               NaN               NaN   
5    2836        高銀               NaN               NaN               NaN   
6    2838      聯邦銀行               NaN               NaN               NaN   
7    2845      遠東商銀               NaN               NaN               NaN   
8    2849      安泰銀行               NaN               NaN               NaN   
9    2855      統一證券               NaN               NaN               NaN   
10   6005       群益證               NaN               NaN               NaN   
11   6024       群益期               NaN               NaN               NaN   
12   1101        台泥           6487864       8.92696e+06       8.60522e+06   
13   1102        亞泥           4658501       6.22901e+06       5.59775e+06   
14   1103        嘉泥             65221             69038             74615   
15   1104      環球水泥            106420            165799            140033   
16   1108      幸福水泥             26663            -22833              7223   
17   1109      信大水泥            389325            742919            618633   
18   1110        東泥             34933             50344             26129   
19   1201      味全公司           1349864       1.46834e+06       1.90504e+06   
20   1203      味王公司            463801            485215            519736   
21   1210      大成長城           2655076       2.51301e+06       2.59035e+06   
22   1215      卜蜂企業            722603            807244            700516   
23   1216        統一          37102312       3.26651e+07       3.94284e+07   
24   1217       愛之味            308201            218439            507713   
25   1218      泰山企業            313782            295501            452851   
26   1219      福壽實業            263446            194488             88870   
27   1220        台榮             68135             90738             81142   
28   1225       福懋油            242787            268049            161394   
29   1227        佳格           2235865       2.26797e+06       2.30653e+06   
30   1229      聯華實業            201314            218734            203929   
31   1231      聯華食品            443541            495312            510968   
32   1232       大統益            567605            550277            417345   
33   1233        天仁            331040            308684            318159   
34   1234        黑松            446503            244519            793305   
35   1235        興泰                89              -358             27192   
36   1236      宏亞食品            123815            188371            119173   
37   1256   鮮活果汁-KY            247025            199761            390641   
38   1262     綠悅-KY            -45818            -52705            -17231   
39   1301        台塑           8147624       8.00273e+06       8.43676e+06   
40   1303      南亞塑膠           6515317       8.66488e+06       1.29055e+07   
41   1304        台聚           1560360            865732       1.21496e+06   
42   1305        華夏            448517            397455            535326   
43   1307      三芳化工            530041            501290            463356   
44   1308        亞聚            176893            102214             40806   
45   1309      台達化工            393182             -4400            205168   
46   1310        台苯            448128            137818            670997   
47   1312      國喬石化            691297            607280       1.26915e+06   
48   1313        聯成            242260            337090            728187   
49   1314       中石化            307990            734086       1.79727e+06   
50   1315      達新工業             81941             86946            130886   
5

In [6]:
df_gross_profit_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'GrossProfit', u'營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
('year:', 107)
('season:', 4)
營業毛利（毛損）
('year:', 107)
('season:', 3)
營業毛利（毛損）
('year:', 107)
('season:', 2)
營業毛利（毛損）
('year:', 107)
('season:', 1)
營業毛利（毛損）
('year:', 106)
('season:', 4)
營業毛利（毛損）
('year:', 106)
('season:', 3)
營業毛利（毛損）
('year:', 106)
('season:', 2)
營業毛利（毛損）
('year:', 106)
('season:', 1)
營業毛利（毛損）
('year:', 105)
('season:', 4)
營業毛利（毛損）
('year:', 105)
('season:', 3)
營業毛利（毛損）
('year:', 105)
('season:', 2)
營業毛利（毛損）
('year:', 105)
('season:', 1)


公司代號    公司名稱 GrossProfit_108Q1 GrossProfit_107Q4 GrossProfit_107Q3  \
0    6015    宏遠證券               NaN               NaN               NaN   
1    6016    康和證券               NaN               NaN               NaN   
2    6020     大展證               NaN               NaN               NaN   
3    6021     大慶證               NaN               NaN               NaN   
4    6023    元大期貨               NaN               NaN               NaN   
5    6026    福邦證券               NaN               NaN               NaN   
6    1258   其祥-KY            114349            334755            254764   
7    1259      安心            320495           1357233            984590   
8    1264      德麥            346754           1466048           1085347   
9    1333     恩得利             24325             63781             43908   
10   1336      台翰             69217            430140            317409   
11   1565    精華光學            587156           2496398           1851110   
12   1566      捷邦            207987            766013            546061   
13   1569      濱川            160247            679218            455611   
14   1570    力肯實業             27169            168917            127341   
15   1580    新麥企業            343871           1718306           1257335   
16   1584    精剛精密              2794              6494              3894   
17   1586    和勤精機             34485            457402            358488   
18   1591   駿吉-KY             25343            130771             87410   
19   1593      祺驊             55996            246631            173768   
20   1595    川寶科技             83641            532327            406787   
21   1597      直得            146514            988326            792416   
22   1599     宏佳騰            139920            638117            508786   
23   1742      台蠟             28637            -31788            -38442   
24   1752      南光            114736            499515            384805   
25   1777      生泰             68504            250840            184111   
26   1781    合世生醫              9929             62261             46087   
27   1784    訊聯生技            106995            443030            322833   
28   1785     光洋科            693069           2247894           1694410   
29   1787     福盈科            143149            620053            470624   
30   1788    杏昌生技            183895            684000            512625   
31   1795    美時製藥           1079091           3139480           2282063   
32   1799      易威             14055             50696             39424   
33   1813     寶利徠             31867             65906             49611   
34   1815    富喬工業            265335           1376302           1071661   
35   2035    唐榮公司            -60308          -1059810           -520572   
36   2061      風青             11974             54562             42870   
37   2063      世鎧             81682            340058            266420   
38   2064      晉椿             10525            211629            160401   
39   2066      世德            180741            488088            334757   
40   2067      嘉鋼             29050            271802            199825   
41   2221    大甲永和             75430            308468            235076   
42   2230      泰茂             19134             99578             69698   
43   2233      宇隆            222979            960337            760452   
44   2235      謚源             54564            181732            129949   
45   2596    綠意開發               724            503701            495657   
46   2640     大車隊            224291            849634            636818   
47   2641    正德海運             50471            205810            150157   
48   2643      捷迅             70924            282952            200764   
49   2718      晶悅              7949             10515               -68   
50   2719     燦星旅             67370            272976            229496   
51   2724   富驛-KY             14990             41890             18898   
52   2726   雅茗-KY            2

In [7]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_gross_profit_otc.columns # the column index
#idx = df_gross_profit_otc.index # the row index
numOfRows_o = df_gross_profit_otc.shape[0] #len(df_gross_profit_otc) #len(df_gross_profit_otc.index)
numOfColumns_o = df_gross_profit_otc.shape[1] #len(df_gross_profit_otc.columns)
headNameOfColumns_o = df_gross_profit_otc.columns

print(numOfColumns_o)
df_gross_profit_otc

for row_index_o in range(0, numOfRows_o):
    for col_index_o in range(0, numOfColumns_o):
        #print(df_gross_profit_otc.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_gross_profit_otc.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_gross_profit_otc.columns.values[col_index_o]): # if (df_gross_profit_otc.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_gross_profit_otc.columns.values[col_index_o]):
                continue
            elif (u"公司名稱" in df_gross_profit_otc.columns.values[col_index_o]):
                continue
            elif (col_index_o == numOfColumns_o-1):
                continue
            else:
                df_gross_profit_otc.iloc[row_index_o, col_index_o] = float(df_gross_profit_otc.iloc[row_index_o, col_index_o]) - float(df_gross_profit_otc.iloc[row_index_o, col_index_o+1])

df_gross_profit_otc              

15


公司代號    公司名稱 GrossProfit_108Q1 GrossProfit_107Q4 GrossProfit_107Q3  \
0    6015    宏遠證券               NaN               NaN               NaN   
1    6016    康和證券               NaN               NaN               NaN   
2    6020     大展證               NaN               NaN               NaN   
3    6021     大慶證               NaN               NaN               NaN   
4    6023    元大期貨               NaN               NaN               NaN   
5    6026    福邦證券               NaN               NaN               NaN   
6    1258   其祥-KY            114349             79991             46960   
7    1259      安心            320495            372643            351366   
8    1264      德麥            346754            380701            372123   
9    1333     恩得利             24325             19873             22109   
10   1336      台翰             69217            112731            133089   
11   1565    精華光學            587156            645288            636955   
12   1566      捷邦            207987            219952            206569   
13   1569      濱川            160247            223607            163390   
14   1570    力肯實業             27169             41576             53997   
15   1580    新麥企業            343871            460971            461482   
16   1584    精剛精密              2794              2600              6614   
17   1586    和勤精機             34485             98914            137162   
18   1591   駿吉-KY             25343             43361             42404   
19   1593      祺驊             55996             72863             83509   
20   1595    川寶科技             83641            125540            148566   
21   1597      直得            146514            195910            265797   
22   1599     宏佳騰            139920            129331            311547   
23   1742      台蠟             28637              6654             -6794   
24   1752      南光            114736            114710            111718   
25   1777      生泰             68504             66729             56116   
26   1781    合世生醫              9929             16174             24985   
27   1784    訊聯生技            106995            120197            107570   
28   1785     光洋科            693069            553484            641306   
29   1787     福盈科            143149            149429            153173   
30   1788    杏昌生技            183895            171375            162832   
31   1795    美時製藥           1079091            857417            815898   
32   1799      易威             14055             11272             22103   
33   1813     寶利徠             31867             16295             15081   
34   1815    富喬工業            265335            304641            409404   
35   2035    唐榮公司            -60308           -539238           -452823   
36   2061      風青             11974             11692              5703   
37   2063      世鎧             81682             73638            105019   
38   2064      晉椿             10525             51228             48189   
39   2066      世德            180741            153331            171261   
40   2067      嘉鋼             29050             71977             74559   
41   2221    大甲永和             75430             73392             93840   
42   2230      泰茂             19134             29880             28724   
43   2233      宇隆            222979            199885            229880   
44   2235      謚源             54564             51783             48619   
45   2596    綠意開發               724              8044             11561   
46   2640     大車隊            224291            212816            212087   
47   2641    正德海運             50471             55653             64243   
48   2643      捷迅             70924             82188             76212   
49   2718      晶悅              7949             10583             -1367   
50   2719     燦星旅             67370             43480             78980   
51   2724   富驛-KY             14990             22992             17359   
52   2726   雅茗-KY            2

In [8]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號      公司名稱 GrossProfit_108Q1 GrossProfit_107Q4 GrossProfit_107Q3  \
0     2801      彰化銀行               NaN               NaN               NaN   
1     2809      京城銀行               NaN               NaN               NaN   
2     2812      台中銀行               NaN               NaN               NaN   
3     2820        華票               NaN               NaN               NaN   
4     2834      臺灣企銀               NaN               NaN               NaN   
5     2836        高銀               NaN               NaN               NaN   
6     2838      聯邦銀行               NaN               NaN               NaN   
7     2845      遠東商銀               NaN               NaN               NaN   
8     2849      安泰銀行               NaN               NaN               NaN   
9     2855      統一證券               NaN               NaN               NaN   
10    6005       群益證               NaN               NaN               NaN   
11    6024       群益期               NaN               NaN               NaN   
12    1101        台泥           6487864       8.92696e+06       8.60522e+06   
13    1102        亞泥           4658501       6.22901e+06       5.59775e+06   
14    1103        嘉泥             65221             69038             74615   
15    1104      環球水泥            106420            165799            140033   
16    1108      幸福水泥             26663            -22833              7223   
17    1109      信大水泥            389325            742919            618633   
18    1110        東泥             34933             50344             26129   
19    1201      味全公司           1349864       1.46834e+06       1.90504e+06   
20    1203      味王公司            463801            485215            519736   
21    1210      大成長城           2655076       2.51301e+06       2.59035e+06   
22    1215      卜蜂企業            722603            807244            700516   
23    1216        統一          37102312       3.26651e+07       3.94284e+07   
24    1217       愛之味            308201            218439            507713   
25    1218      泰山企業            313782            295501            452851   
26    1219      福壽實業            263446            194488             88870   
27    1220        台榮             68135             90738             81142   
28    1225       福懋油            242787            268049            161394   
29    1227        佳格           2235865       2.26797e+06       2.30653e+06   
30    1229      聯華實業            201314            218734            203929   
31    1231      聯華食品            443541            495312            510968   
32    1232       大統益            567605            550277            417345   
33    1233        天仁            331040            308684            318159   
34    1234        黑松            446503            244519            793305   
35    1235        興泰                89              -358             27192   
36    1236      宏亞食品            123815            188371            119173   
37    1256   鮮活果汁-KY            247025            199761            390641   
38    1262     綠悅-KY            -45818            -52705            -17231   
39    1301        台塑           8147624       8.00273e+06       8.43676e+06   
40    1303      南亞塑膠           6515317       8.66488e+06       1.29055e+07   
41    1304        台聚           1560360            865732       1.21496e+06   
42    1305        華夏            448517            397455            535326   
43    1307      三芳化工            530041            501290            463356   
44    1308        亞聚            176893            102214             40806   
45    1309      台達化工            393182             -4400            205168   
46    1310        台苯            448128            137818            670997   
47    1312      國喬石化            691297            607280       1.26915e+06   
48    1313        聯成            242260            337090            728187   
49    1314       中石化            307990            734086       1.79727e+06   
50    1315      達新工業        

In [9]:
#檢查column資料型態

#df_eps.info() #non-null object
#df_eps.dtypes #object
#df_eps.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
GrossProfit_104Q4    float64
GrossProfit_104Q3    float64
GrossProfit_104Q2    float64
GrossProfit_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                   int64
公司名稱                  object
GrossProfit_108Q1    float64
GrossProfit_107Q4    float64
GrossProfit_107Q3    float64
GrossProfit_107Q2    float64
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
dtype: object

In [10]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [11]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfit_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfit_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [12]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)])):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [13]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:9: RuntimeWarning: invalid value encountered in double_scalars
  if __name__ == '__main__':


In [14]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [15]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [16]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on=u'公司代號', how='inner')

df_gross_profit

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  GrossProfit_108Q1  GrossProfit_107Q4  GrossProfit_107Q3  \
0     2801      彰化銀行                NaN                NaN                NaN   
1     2809      京城銀行                NaN                NaN                NaN   
2     2812      台中銀行                NaN                NaN                NaN   
3     2820        華票                NaN                NaN                NaN   
4     2834      臺灣企銀                NaN                NaN                NaN   
5     2836        高銀                NaN                NaN                NaN   
6     2838      聯邦銀行                NaN                NaN                NaN   
7     2845      遠東商銀                NaN                NaN                NaN   
8     2849      安泰銀行                NaN                NaN                NaN   
9     2855      統一證券                NaN                NaN                NaN   
10    6005       群益證                NaN                NaN                NaN   
11    6024       群益期                NaN                NaN                NaN   
12    1101        台泥          6487864.0          8926965.0          8605218.0   
13    1102        亞泥          4658501.0          6229011.0          5597747.0   
14    1103        嘉泥            65221.0            69038.0            74615.0   
15    1104      環球水泥           106420.0           165799.0           140033.0   
16    1108      幸福水泥            26663.0           -22833.0             7223.0   
17    1109      信大水泥           389325.0           742919.0           618633.0   
18    1110        東泥            34933.0            50344.0            26129.0   
19    1201      味全公司          1349864.0          1468341.0          1905039.0   
20    1203      味王公司           463801.0           485215.0           519736.0   
21    1210      大成長城          2655076.0          2513010.0          2590353.0   
22    1215      卜蜂企業           722603.0           807244.0           700516.0   
23    1216        統一         37102312.0         32665119.0         39428428.0   
24    1217       愛之味           308201.0           218439.0           507713.0   
25    1218      泰山企業           313782.0           295501.0           452851.0   
26    1219      福壽實業           263446.0           194488.0            88870.0   
27    1220        台榮            68135.0            90738.0            81142.0   
28    1225       福懋油           242787.0           268049.0           161394.0   
29    1227        佳格          2235865.0          2267970.0          2306530.0   
30    1229      聯華實業           201314.0           218734.0           203929.0   
31    1231      聯華食品           443541.0           495312.0           510968.0   
32    1232       大統益           567605.0           550277.0           417345.0   
33    1233        天仁           331040.0           308684.0           318159.0   
34    1234        黑松           446503.0           244519.0           793305.0   
35    1235        興泰               89.0             -358.0            27192.0   
36    1236      宏亞食品           123815.0           188371.0           119173.0   
37    1256   鮮活果汁-KY           247025.0           199761.0           390641.0   
38    1262     綠悅-KY           -45818.0           -52705.0           -17231.0   
39    1301        台塑          8147624.0          8002733.0          8436760.0   
40    1303      南亞塑膠          6515317.0          8664882.0         12905494.0   
41    1304        台聚          1560360.0           865732.0          1214961.0   
42    1305        華夏           448517.0           397455.0           535326.0   
43    1307      三芳化工           530041.0           501290.0           463356.0   
44    1308        亞聚           176893.0           102214.0            40806.0   
45    1309      台達化工           393182.0            -4400.0           205168.0   
46    1310        台苯           448128.0           137818.0           670997.0   
47    1312      國喬石化           691297.0           607280.0          1269154.0   
48    1313        聯成           242260

In [17]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [18]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_GrossProfit.xlsx', 'GrossProfit_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
